# 2025년 9월 29일 6일차 RAG

## chroma DB -CRUD

### chroma DB - Create / Add

In [ ]:
import chromadb
client = chromadb.PersistentClient(path="my_chroma_db")
collection = client.get_or_create_collection(name="my_collection")

- add

In [ ]:
collection.add (
    documents=["apple", "banana"],
    ids = ["1", "2"],
    metadatas=[{"type" : "fruit"}, {"type" : "fruit"}]
)

- update

In [ ]:
collection.update (
    documents=["green apple"],
    ids = ["1"],
    metadatas=[{"type" : "fruit"}]
)

- 특정한 ID만 조회하기

In [ ]:
data = collection.get(ids=["1"])
print(data)

- 전체 데이터 조회하기

In [ ]:
all_data = collection.get()
print(all_data)

- 데이터 삭제

In [ ]:
collection.delete(ids=["1"])

# Data Connection의 개요

- Document loaders : 데이터 소스로부터 문서를 불러온다.
- Document transformers : 문서에 어떤 종류의 변환을 가한다.
- Text embedding models : 문서를 벡터화한다.
- Vector stores : 벡터화된 문서를 저장할 수 있는 저장소
- Retrievers : 입력한 텍스트와 관련된 문서를 검색한다.

- RAG 파이프라인 - Documentloaders

In [ ]:
from langchain.document_loaders import TextLoader

loader = TextLoader('data/data.txt', encoding='utf-8')

documents =loader.load()

print(documents)


- RAG 파이프라인 - Document transformers

In [ ]:
from langchain.text_splitter import CharacterTextSplitter

text_splitter = CharacterTextSplitter(chunk_size=50, chunk_overlap=10)
docs = text_splitter.split_documents(documents)

for i, chunk in enumerate(docs):
    print(i, "--", chunk.page_content)

In [ ]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

text_splitter = RecursiveCharacterTextSplitter(chunk_size=50, chunk_overlap=10)
docs = text_splitter.split_documents(documents)

for i, chunk in enumerate(docs):
    print(i, "--", chunk.page_content)

- RAG 파이프라인 - embedding 
- 텍스트 -> 수치화(벡터 수치화, 의미를 부여한 상태로 의미가 비슷한 것끼리 가까운 장소에 배치)
- LLM 모델 -> 각 모델들은 embedding model들을 가지고 있다

In [ ]:
from dotenv import load_dotenv
import os
load_dotenv(override=True)
api_key = os.getenv("OPENAI_API_KEY")
default_model = os.getenv("OPENAI_DEFAULT_MODEL")

In [ ]:
from langchain_openai import OpenAIEmbeddings

embedding_model = OpenAIEmbeddings()

doc_texts = [doc.page_content for doc in docs]
vector = embedding_model.embed_documents(doc_texts)
print(vector)

In [ ]:
print(len(vector))

- RAG 파이프라인 - vector DB에 저장

In [ ]:
from langchain.vectorstores import Chroma
vectorstore = Chroma.from_documents(documents = docs, 
                      embedding=embedding_model,
                      persist_directory="my_chroma_db")
vectorstore.persist()

- RAG 파이프라인 - Retriever 및 LLM 생성

In [ ]:
from langchain.chat_models import ChatOpenAI

retriever = vectorstore.as_retriever()

llm = ChatOpenAI(api_key=api_key,
           model_name= default_model,
           temperature=0.2)

- RAG Chain

In [ ]:
from langchain.chains import RetrievalQA

qa_chain = RetrievalQA.from_chain_type(llm=llm,
                                       retriever=retriever)

- RAG 파이프라인 - 질문하기

In [ ]:
query = "프랑스의 수도는 어디입니까?"
result = qa_chain.run(query)
print(result)

In [ ]:
query = "나아지리아의 수도는 어디입니까?"
result = qa_chain.run(query)
print(result)

In [ ]:
exists = retriever.get_relevant_documents(query)
if not exists :
    print("No relevant documents found.")
else:
    print(result)

- 없는 데이터 질문했을 때

In [ ]:
from langchain.prompts import PromptTemplate

custom_prompt = PromptTemplate(
    input_variables=["context", "question"],
    template="""
    너는 주어진 context(문서)에서만 답변해야 해. 만약 context가 비어 있거나,
    context에 답이 없으면 반드시 "그런 내용 없습니다."라고 답해.
    Context: {context}
    Question: {question}
    답변:"""
)

qa_chain = RetrievalQA.from_chain_type(llm=llm,
                                       chain_type_kwargs={"prompt" : custom_prompt},
                                       retriever=retriever)
query = "오스트리아의 수도는 어디입니까?"
result = qa_chain.run(query)
print(result)


# 전체적인 Pipeline 절차

In [97]:
from dotenv import load_dotenv
import os
load_dotenv(override=True)
api_key = os.getenv("OPENAI_API_KEY")
default_model = os.getenv("OPENAI_DEFAULT_MODEL")

from langchain.document_loaders import TextLoader

loader = TextLoader('data/data.txt', encoding='utf-8')

documents =loader.load()

print(documents)

from langchain.text_splitter import RecursiveCharacterTextSplitter

text_splitter = RecursiveCharacterTextSplitter(chunk_size=50, chunk_overlap=10)
docs = text_splitter.split_documents(documents)

for i, chunk in enumerate(docs):
    print(i, "--", chunk.page_content)

from langchain_openai import OpenAIEmbeddings

embedding_model = OpenAIEmbeddings()

doc_texts = [doc.page_content for doc in docs]
vector = embedding_model.embed_documents(doc_texts)
print(vector)

from langchain.vectorstores import Chroma
vectorstore = Chroma.from_documents(documents = docs, 
                      embedding=embedding_model,
                      persist_directory="my_chroma_db")
vectorstore.persist()

from langchain.chat_models import ChatOpenAI

retriever = vectorstore.as_retriever()

llm = ChatOpenAI(api_key=api_key,
           model_name= default_model,
           temperature=0.2)

from langchain.prompts import PromptTemplate
from langchain.chains import RetrievalQA

custom_prompt = PromptTemplate(
    input_variables=["context", "question"],
    template="""
    너는 주어진 context(문서)에서만 답변해야 해. 만약 context가 비어 있거나,
    context에 답이 없으면 반드시 "그런 내용 없습니다."라고 답해.
    Context: {context}
    Question: {question}
    답변:"""
)

qa_chain = RetrievalQA.from_chain_type(llm=llm,
                                       chain_type_kwargs={"prompt" : custom_prompt},
                                       retriever=retriever)
query = "영국의 수도는 어디입니까?"
result = qa_chain.run(query)
print(result)


[Document(metadata={'source': 'data/data.txt'}, page_content='프랑스의 수도는 파리이다. 파리는 유럽에서 가장 인기 있는 관광 도시 중 하나로, 에펠탑과 루브르 박물관이 유명하다.\n\n독일의 수도는 베를린이다. 베를린은 역사적으로 중요한 도시이며, 베를린 장벽으로 유명하다.\n\n일본의 수도는 도쿄이다. 도쿄는 기술과 문화의 중심지로, 애니메이션과 음식 문화가 발달해 있다.')]
0 -- 프랑스의 수도는 파리이다. 파리는 유럽에서 가장 인기 있는 관광 도시 중 하나로, 에펠탑과
1 -- 하나로, 에펠탑과 루브르 박물관이 유명하다.
2 -- 독일의 수도는 베를린이다. 베를린은 역사적으로 중요한 도시이며, 베를린 장벽으로
3 -- 베를린 장벽으로 유명하다.
4 -- 일본의 수도는 도쿄이다. 도쿄는 기술과 문화의 중심지로, 애니메이션과 음식 문화가 발달해
5 -- 문화가 발달해 있다.
[[0.0037829740904271603, 0.016250282526016235, 0.017314771190285683, -0.04821186512708664, -0.0026494294870644808, 0.04001935198903084, -0.021532298997044563, 0.008670859970152378, 0.01700485683977604, -0.01833883486688137, -0.007000017911195755, 0.01573825068771839, 0.01744951494038105, -0.026113638654351234, -0.014417747035622597, -0.01656019687652588, 0.008738232776522636, -0.005359494127333164, 8.487374543619808e-06, -0.00400530407205224, -0.00535612553358078, -0.00603658938780427, 0.014498594217002392, 0.003729076124727

- 위키피디아 - 아이유 - 내용 스크래핑 해오세요

In [68]:
import requests
from bs4 import BeautifulSoup

# 1. 크롤링할 위키피디아 URL 지정
url = 'https://ko.wikipedia.org/wiki/%EC%95%84%EC%9D%B4%EC%9C%A0'

# 2. 실제 브라우저처럼 보이게 할 User-Agent 설정
headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.36'
}

# 3. requests.get() 호출 시 headers= 파라미터 추가
try:
    # 헤더를 포함하여 GET 요청 보내기
    response = requests.get(url, headers=headers)
    response.raise_for_status()  # 200번대 상태 코드가 아니면 오류 발생

    # 4. BeautifulSoup으로 HTML 파싱
    soup = BeautifulSoup(response.text, 'html.parser')

    # 5. 원하는 정보 추출 (핵심 변경 부분)
    # 본문 내용이 포함된 div 태그를 class 이름으로 찾기
    content = soup.find('div', class_='mw-page-container') 
    
    # 해당 태그 안의 모든 텍스트를 가져오기
    # separator='\n'을 추가하면 각 줄을 바꿔서 더 보기 좋게 출력됩니다.
    full_text = content.get_text(separator='\n', strip=True)

    # 6. 결과 출력
    print(full_text)
    print("\n\n성공적으로 페이지 본문을 크롤링했습니다!")

except requests.exceptions.HTTPError as err:
    print(f"HTTP 오류가 발생했습니다: {err}")
except requests.exceptions.RequestException as e:
    print(f"요청 중 오류가 발생했습니다: {e}")

목차
사이드바로 이동
숨기기
처음 위치
1
학력
2
활동
활동 하위섹션 토글하기
2.1
2008-2010
2.2
2011-2013
2.3
2014-2016
2.4
2017-2018
2.5
2019-2020
2.6
2021-2022
2.7
2023-2024
2.8
2025
3
음반 목록
4
음반 외 활동 목록
5
수상 및 후보 목록
6
사건
7
같이 보기
8
각주
각주 하위섹션 토글하기
8.1
내용주
8.2
참조주
9
외부 링크
목차 토글
아이유
63개 언어
العربية
مصرى
تۆرکجه
Basa Bali
Bikol Central
Български
Català
Cebuano
کوردی
Čeština
Dansk
Deutsch
Kadazandusun
Ελληνικά
English
Esperanto
Español
Eesti
Euskara
فارسی
Suomi
Français
हिन्दी
Kreyòl ayisyen
Magyar
Հայերեն
Interlingua
Bahasa Indonesia
Italiano
日本語
Jawa
Қазақша
کٲشُر
Latina
Māori
മലയാളം
Монгол
Bahasa Melayu
မြန်မာဘာသာ
Nederlands
Norsk bokmål
Polski
Português
Română
Русский
Simple English
Slovenčina
Soomaaliga
Српски / srpski
Sesotho
Sunda
Svenska
தமிழ்
ไทย
Tagalog
Setswana
Türkçe
Українська
Oʻzbekcha / ўзбекча
Tiếng Việt
中文
閩南語 / Bân-lâm-gí
粵語
링크 편집
문서
토론
한국어
읽기
원본 보기
역사 보기
도구
도구
사이드바로 이동
숨기기
동작
읽기
원본 보기
역사 보기
일반
여기를 가리키는 문서
가리키는 글의 최근 바뀜
파일 올리기
고유 링크
문서 정보
이 문서 인용하기
축약된 URL 얻기
QR코드 다운로드
인쇄/내보내기
책 만들기
PDF로 다운로드
인쇄용 판
다른 프로

In [98]:
def data_loader():
    import requests
    from bs4 import BeautifulSoup

    # 1. 크롤링할 위키피디아 URL 지정
    url = 'https://ko.wikipedia.org/wiki/%EC%95%84%EC%9D%B4%EC%9C%A0'

    # 2. 실제 브라우저처럼 보이게 할 User-Agent 설정
    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.36'
    }

    # 3. requests.get() 호출 시 headers= 파라미터 추가
    
        # 헤더를 포함하여 GET 요청 보내기
    response = requests.get(url, headers=headers)
    response.raise_for_status()  # 200번대 상태 코드가 아니면 오류 발생

        # 4. BeautifulSoup으로 HTML 파싱
    soup = BeautifulSoup(response.text, 'html.parser')
    text = soup.select_one('#mw-content-text')
    
        
        # 해당 태그 안의 모든 텍스트를 가져오기
        # separator='\n'을 추가하면 각 줄을 바꿔서 더 보기 좋게 출력됩니다.
    full_text = text.get_text(separator='\n', strip=True)

        # 6. 결과 출력
        
    return full_text

In [99]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_core.documents import Document

def data_transformer(text, chunk_size=200, chunk_overlap=50):
    splitter = RecursiveCharacterTextSplitter(chunk_size=chunk_size,
                                              chunk_overlap=chunk_overlap)
    chunks = splitter.split_text(text)
    docs = [Document(page_content=chunk) for chunk in chunks]
    return docs

In [100]:
embedding_model = OpenAIEmbeddings()
doc_texts = [doc.page_content for doc in docs]
vector = embedding_model.embed_documents(doc_texts)

In [101]:
from langchain_community.embeddings import OpenAIEmbeddings
from langchain.vectorstores import Chroma

def data_embedding_and_vectorstore(docs):
    embedding_model = OpenAIEmbeddings()
    vectordb = Chroma.from_documents(documents=docs,
                                     embedding=embedding_model,
                                     persist_directory='my_iu_db')
    vectordb.persist()
    return vectordb

In [106]:

def data_retriever_chain(vectordb) :
    retriever = vectordb.as_retriever()
    llm = ChatOpenAI(model="gpt-4o", temperature=0.2)
    qa_chain = RetrievalQA.from_chain_type(llm=llm,
                                           retriever=retriever)
    return qa_chain

In [107]:
# Data loader
print("Data Loading")
text = data_loader()
print(text)

# Data transformer
print('Data Transforming')
docs = data_transformer(text, 200, 50)
print(docs)

#embedding
print("Data Embedding")
vectordb = data_embedding_and_vectorstore(docs)

# retriever & RAG chain
qa_chain = data_retriever_chain(vectordb)
# question

Data Loading
다른 뜻에 대해서는
아이유 (동음이의)
문서를 참고하십시오.
IU
는 여기로 연결됩니다. 다른 뜻에 대해서는
IU (동음이의)
문서를 참고하십시오.
아이유
2022년 11월 25일
청룡영화상
에서의 아이유
기본 정보
본명
이지은
출생
1993년 5월 16일
(
1993-05-16
)
(32세)
대한민국
서울특별시
성동구
송정동
성별
여성
직업
가수
,
배우
장르
댄스
,
발라드
,
어쿠스틱
,
R&B
활동 시기
2008년~
학력
동덕여자고등학교
(졸업)
레이블
카카오엔터테인먼트
,
EMI 뮤직 재팬
소속사
EDAM 엔터테인먼트
서명
웹사이트
edam-ent
.com
유튜브
채널
이지금 [IU Official
]
분야
일상
,
음악
개설일
2017년 2월 13일
구독자 수
978만 명
(2024년 10월 6일 기준)
총 조회수
3,150,968,674회
(2024년 10월 6일 기준)
v
t
e
아이유
(
IU
,
본명
:
이지은, 李知恩
[
1
]
,
1993년
5월 16일
~)는
대한민국
의 싱어송라이터, 작곡가, 배우이다. 2007년 로엔 엔터테인먼트(현
카카오 엔터테인먼트
) 연습생으로 전속 계약을 맺고 15세의 나이에 2008년 첫 EP인 로스트 앤 파운드(Lost and Found)를 통해 가수로 데뷔했다.
학력
동덕여자고등학교
졸업
활동
2008-2010
2009년 7월 5일에
핫트랙스
잠실점에서 개최된 팬사인회에서의 아이유
아이유는 2008년 9월 18일 엠넷 M! Countdown에서 데뷔 싱글 "미아"로 데뷔하였고
2008년
9월 23일
에 발매된 첫 번째
미니 음반
Lost and Found
를 발매하였다. 데뷔 전부터 라디오에서 음악을 알렸던 아이유는
유영석
,
유희열
,
정재형
등의 많은 음악가로부터 호평을 받았다.
유영석
은 "나이가 어린 소녀인데 노래를 너무 잘하고, 음악성이 뛰어난 것 같아서 이 앨범을 추천한다"라고 칭찬하였으며,
정재형
은 "앞으로 많은 발전이 기대되는 가수"라며 기대감을 보였다.
[
2
]


In [108]:
for i in range(5):
    query = input("아이유에 대한 질문을 입력하세요 : ")
    result = qa_chain.run(query)
    print(result)

죄송하지만, 아이유의 가족에 대한 구체적인 정보는 제공되지 않았습니다.
아이유는 이담엔터테인먼트와 전속계약을 맺고 있습니다.
아이유는 1993년 5월 16일에 태어났습니다. 따라서 2025년 기준으로 아이유는 만 31세입니다.
죄송하지만, 아이유가 가장 최근에 출연한 영화에 대한 정보는 제공된 문맥에서 찾을 수 없습니다.
아이유가 출연한 드라마 중 하나는 SBS TV 드라마 《달의 연인 - 보보경심 려》입니다. 이 드라마에서 아이유는 주연을 맡아 연기하였습니다.


# RAG - PDF

In [119]:
from langchain_community.document_loaders import PyPDFLoader
# Data loader
loader = PyPDFLoader("data/Forouzan.pdf")
documents = loader.load()

# Data transformer
splitter = RecursiveCharacterTextSplitter(chunk_size = 200, chunk_overlap = 50)
docs = splitter.split_documents(documents)
print(docs)
# embedding % vectorstore
embedding_model = OpenAIEmbeddings()
vectordb = Chroma.from_documents(documents=docs,
                                 embedding=embedding_model,
                                 persist_directory="my_fifa_db")
vectordb.persist()

# retriever & RAG chain
retriever = vectordb.as_retriever(search_kwargs={"k": 5})
llm = ChatOpenAI(model="gpt-4o", temperature=0.2)
qa_chain = RetrievalQA.from_chain_type(llm=llm, chain_type="stuff", retriever=retriever)
#question

[Document(metadata={'producer': 'PDFTron PDFNet, V7.10742', 'creator': 'PyPDF', 'creationdate': '2013-08-01T13:36:51+00:00', 'moddate': '2020-04-24T15:20:31+00:00', 'author': 'iccp2_134', 'title': 'for38482_fm.fm', 'source': 'data/Forouzan.pdf', 'total_pages': 752, 'page': 0, 'page_label': '1'}, page_content='INTRODUCTION\nTO\nCRYPTOGRAPHY\nAND\nNETWORK SECURITY'), Document(metadata={'producer': 'PDFTron PDFNet, V7.10742', 'creator': 'PyPDF', 'creationdate': '2013-08-01T13:36:51+00:00', 'moddate': '2020-04-24T15:20:31+00:00', 'author': 'iccp2_134', 'title': 'for38482_fm.fm', 'source': 'data/Forouzan.pdf', 'total_pages': 752, 'page': 1, 'page_label': '2'}, page_content='McGraw-Hill Forouzan Networking Series\nTitles by Behrouz A. Forouzan:\nCryptography and Network Security\nData Communications and Networking\nTCP/IP Protocol Suite\nLocal Area Networks'), Document(metadata={'producer': 'PDFTron PDFNet, V7.10742', 'creator': 'PyPDF', 'creationdate': '2013-08-01T13:36:51+00:00', 'moddate'

In [120]:
query = "암호학의 종류에는 뭐가 있어?"
result = qa_chain.run(query)
print(result)

암호학의 종류에는 여러 가지가 있지만, 특히 암호 해독(cryptanalysis) 공격의 유형으로는 다음과 같은 네 가지가 있습니다:

1. 암호문 단독 공격(ciphertext-only attack)
2. 기지 평문 공격(known-plaintext attack)
3. 선택 평문 공격(chosen-plaintext attack)
4. 선택 암호문 공격(chosen-ciphertext attack)

이러한 공격 유형들은 암호 시스템의 취약성을 평가하고 더 나은 비밀 코드를 만드는 데 도움을 줍니다.


- 유사도 검사

In [123]:
from langchain.embeddings import OpenAIEmbeddings
import numpy as np
from itertools import combinations

#1. 임베딩 생성기 준비
embeddings = OpenAIEmbeddings()

#2. 문장 리스트
sentences = [
    "안녕하세요? 반갑습니다.",
    "안녕하세요? 반갑습니다!",
    "안녕하세요? 만나서 반가워요.",
    "Hi, nice to meet you.",
    "I like to eat apples."
]

#3. 각 문장을 임베딩 벡터로 변환
sentence_vectors = [embeddings.embed_query(sentence) for sentence in sentences]

#4. 코사인 유사도 함수 정의
def cosine_similarity(vec1, vec2):
    vec1 = np.array(vec1)
    vec2 = np.array(vec2)
    return np.dot(vec1, vec2) / (np.linalg.norm(vec1) * np.linalg.norm(vec2))

#5. 모든 문장 쌍에 대해 코사인 유사도 계산 및 출력
print("문장 쌍별 코사인 유사도:")
for (i, j) in combinations(range(len(sentences)), 2):
    sim = cosine_similarity(sentence_vectors[i], sentence_vectors[j])
    print(f"[{i+1}] \"{sentences[i]}\" <-> [{j+1}] \"{sentences[j]}\" : {sim:.4f}")

문장 쌍별 코사인 유사도:
[1] "안녕하세요? 반갑습니다." <-> [2] "안녕하세요? 반갑습니다!" : 0.9881
[1] "안녕하세요? 반갑습니다." <-> [3] "안녕하세요? 만나서 반가워요." : 0.9463
[1] "안녕하세요? 반갑습니다." <-> [4] "Hi, nice to meet you." : 0.8447
[1] "안녕하세요? 반갑습니다." <-> [5] "I like to eat apples." : 0.7296
[2] "안녕하세요? 반갑습니다!" <-> [3] "안녕하세요? 만나서 반가워요." : 0.9379
[2] "안녕하세요? 반갑습니다!" <-> [4] "Hi, nice to meet you." : 0.8359
[2] "안녕하세요? 반갑습니다!" <-> [5] "I like to eat apples." : 0.7265
[3] "안녕하세요? 만나서 반가워요." <-> [4] "Hi, nice to meet you." : 0.8372
[3] "안녕하세요? 만나서 반가워요." <-> [5] "I like to eat apples." : 0.7126
[4] "Hi, nice to meet you." <-> [5] "I like to eat apples." : 0.7776


- WIKIPEDIA 검색 agent

In [126]:
from langchain.agents import load_tools, initialize_agent, AgentType

chat = ChatOpenAI(temperature=0.5, 
                max_tokens=2048, 
                model_name="gpt-4o")

#agent가 위키피디아 검색 도구를 사용할 수 있게 만든다 
tools = load_tools(["wikipedia"], llm=chat)

#agent가 객체 생성 
agent = initialize_agent(
    #질문을 이해하고, 필요할 때 도구(여기서는 위키피디아)를 스스로 활용
    tools, 
    chat, 
    agent_type=AgentType.ZERO_SHOT_REACT_DESCRIPTION,
    description="계산이 필요할 때 사용", #agent의 역할 설명
    verbose=True  #실행 과정을 상세하게 출력
)
agent.run('아이유는 몇살이야?')



> Entering new AgentExecutor chain...
아이유의 출생 연도를 알아야 나이를 계산할 수 있습니다. 아이유의 출생 연도를 확인하기 위해 Wikipedia를 검색하겠습니다.
Action: wikipedia
Action Input: 아이유
Observation: Page: IU (entertainer)
Summary: Lee Ji-eun (Korean: 이지은; born May 16, 1993), also known by her stage name IU (아이유), is a South Korean singer-songwriter and actress. She signed with LOEN Entertainment (now Kakao Entertainment) in 2007 as a trainee and debuted as a singer at the age of fifteen with the EP Lost and Found (2008). Although her follow-up albums brought mainstream success, it was only after the release of "Good Day", the lead single from her 2010 album Real, that she achieved national stardom. "Good Day" went on to spend five consecutive weeks at the top of South Korea's Gaon Digital Chart, and in 2019, it was ranked number one on Billboard's "100 Greatest K-Pop Songs of the 2010s" list.
With the success of her 2011 albums, Real+ and Last Fantasy, IU established herself as a formidable force on the music charts of her

'아이유는 만 30세입니다.'

In [139]:
from langchain_openai import ChatOpenAI  
from langchain.agents import AgentExecutor, create_react_agent  
from langchain_core.prompts import PromptTemplate
from langchain_core.tools import Tool  
import openai 
import os


chat = ChatOpenAI(
    temperature=0.7, 
    max_tokens=2048, 
    model="gpt-4-turbo"  
)

# DALL·E 함수를 직접 정의
def generate_image(prompt: str) -> str:
    """DALL·E를 사용하여 이미지 생성"""
    try:
        client = openai.OpenAI()
        response = client.images.generate(
            model="dall-e-3",
            prompt=prompt,
            size="1024x1024",
            quality="standard",
            n=1,
        )
        image_url = response.data[0].url
        return f"이미지가 생성되었습니다. URL: {image_url}"
    except Exception as e:
        return f"이미지 생성 중 오류 발생: {str(e)}"

# Tool 객체로 래핑
dalle_tool = Tool(
    name="DALL-E Image Generator",
    description="텍스트 설명을 바탕으로 이미지를 생성합니다. 사용법: 생성하고 싶은 이미지의 상세한 설명을 입력하세요.",
    func=generate_image
)
tools = [dalle_tool]

# 프롬프트 템플릿 정의
prompt = PromptTemplate.from_template("""
당신은 DALL·E를 사용하여 이미지를 생성하는 전문가입니다.
사용자의 요청에 따라 적절한 이미지를 생성해주세요.

사용 가능한 도구:
{tools}

도구 이름: {tool_names}

다음 형식을 사용하세요:

Question: 답해야 할 질문
Thought: 무엇을 해야 하는지 생각해보세요
Action: 취할 행동 [{tool_names} 중 하나]
Action Input: 행동의 입력
Observation: 행동의 결과
... (이 Thought/Action/Action Input/Observation을 필요한 만큼 반복)
Thought: 이제 최종 답을 알았습니다
Final Answer: 원래 질문에 대한 최종 답

시작하세요!

Question: {input}
Thought: {agent_scratchpad}
""")


agent = create_react_agent(chat, tools, prompt)

agent_executor = AgentExecutor(
    agent=agent,
    tools=tools,
    verbose=True,
    max_iterations=3,
    handle_parsing_errors=True
)

# 이미지 생성 명령 실행
try:
    result = agent_executor.invoke({
        "input": "검술을 하는 기사들을 그려줘"
    })
    print("\n" + "="*50)
    print(result["output"])
    
except Exception as e:
    print(f"오류 발생: {str(e)}")



> Entering new AgentExecutor chain...
Thought: 사용자가 요청한 이미지는 검술을 하는 기사들을 표현하는 것이므로, 중세 스타일의 갑옷을 입은 기사들이 검을 사용하여 대결하는 모습을 그려야겠다. 배경은 오픈 필드나 성의 내부일 수 있으며, 다이내믹하고 흥미로운 포즈를 사용해야 한다.

Action: DALL-E Image Generator
Action Input: 중세 스타일의 갑옷을 입은 두 기사가 검을 들고 대결하는 모습, 배경은 성 내부, 강렬한 표정과 동적인 자세이미지 생성 중 오류 발생: Error code: 400 - {'error': {'message': 'Your request was rejected as a result of our safety system. Image descriptions generated from your prompt may contain text that is not allowed by our safety system. If you believe this was done in error, your request may succeed if retried, or by adjusting your prompt.', 'type': 'image_generation_user_error', 'param': None, 'code': 'content_policy_violation'}}생성 요청이 안전 시스템에 거부되었다는 것을 알게 되었습니다. 사용자의 요청은 기사들이 검을 들고 대결하는 모습이지만, 이러한 내용이 폭력적인 행위를 묘사할 수 있기 때문에 거부된 것 같습니다. 따라서, 더 평화로운 씬이나 대결 대신 연습하는 모습으로 설명을 수정해야 할 필요가 있습니다.

Action: DALL-E Image Generator
Action Input: 중세 스타일의 갑옷을 입은 두 기사가 검술 연습을 하는 평화로운 모습, 배경은 성 내부, 진지하지만 평화로운 표정과 포즈이미지가 생성되었습니다. URL: h

- FAISS

In [140]:
import faiss
import pypdf
import sentence_transformers



c:\Users\edukd\miniconda3\envs\myKDA2\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


KeyboardInterrupt: 

In [137]:
from langchain.document_loaders import PyPDFLoader
loader = PyPDFLoader("data/The_Adventures_of_Tom_Sawyer.pdf")
documents = loader.load()
print(documents[5].page_content[:1000])

Chapter 1    The Fence 
 
Tom Sawyer lived with his aunt because his mother and 
father were dead. Tom didn’t like going to school, and he 
didn’t like working. He liked playing and having 
adventures. One Friday, he didn’t go to school—he went 
to the river. 
Aunt Polly was angry. “You’re a bad boy!” she said. 
“Tomorrow you can’t play with your friends because you 
didn’t go to school today. Tomorrow you’re going to work 
for me. You can paint the fence.” 
Saturday morning, Tom was not happy, but he started to 
paint the fence. His friend Jim was in the street. 
Tom asked him, “Do you want to paint?” 
Jim said, “No, I can’t. I’m going to get water.” 
Then Ben came to Tom’s house. He watched Tom and 
said, “I’m going to swim today. You can’t swim because 
you’re working.” 
Tom said, “This isn’t work. I like painting.” 
“Can I paint, too?” Ben asked. 
“No, you can’t,” Tom answered. “Aunt Polly asked me 
because I’m a very good painter.” 
Ben said, “I’m a good painter, too. Please, can 

In [141]:
text = "마을 무덤에 있던 남자를 죽인 사람은 누구니?"
text_embedding = embeddings.embed_query(text)
print(text_embedding)
print(len(text_embedding))

[0.007235634975654354, -0.020684336968037138, 0.018302662054393373, -0.022807135874352128, -0.019622938446202203, 0.031117112892811084, -0.025214699692580354, 0.01717654220241984, -0.01854859454075248, -0.004860430891172863, -0.0048927906249196, 0.008309977949781519, 0.0031761072618825973, 0.004633912754945702, 0.01113821830671733, 0.02388147791715673, 0.024813437504004714, -0.0130280254536752, 0.02115031676146113, -0.04066970517726085, 0.012969778677989123, 0.0018962799551805868, -0.005750323569208138, 0.003121095667947016, 0.009138386574904454, 0.03903877310630919, 0.019079293801669943, -0.017992008237895672, 0.014807810809745749, -0.004831307037668543, 0.021797511436395873, -0.005371714404974543, -0.010542798646983827, -0.02502054129009993, -0.032773930143056955, 0.030418142271352533, 0.007941076426275177, -0.0020920564141975392, -0.000992634553284397, -0.0018331785442236412, 0.009241937536629502, -0.012432606725264259, 0.010905227478682772, -0.03448252333982663, 0.00416793296152171

In [143]:
from langchain.vectorstores import FAISS
from langchain.embeddings import OpenAIEmbeddings

embedding = OpenAIEmbeddings()
db = FAISS.from_documents(documents, embedding)

In [144]:
llm = ChatOpenAI(model= "gpt-4o", max_tokens=2048, temperature=0.2)
retriever = db.as_retriever(search_kwargs={"k":5})

qa_chain = RetrievalQA.from_chain_type(llm=llm,
                                       chain_type="stuff",
                                       retriever=retriever)

In [145]:
query = "마을 무덤에 있던 남자를 죽인 사람은 누구니?"
result = qa_chain.run(query)
print(result)

무덤에 있던 남자를 죽인 사람은 인디언 조입니다.


- LLAMA index
- GPT index RAG를 만들기 위해 정보를 검색해주는 프레임 워크

In [146]:
from llama_index.core import VectorStoreIndex, SimpleDirectoryReader

#1. 데이터 폴더에서 문서 읽기
pdf_file = [".\\data\\The_Adventures_of_Tom_Sawyer.pdf"]
documents = SimpleDirectoryReader(input_files=pdf_file).load_data()
for doc in documents:
    print(doc.text[:500])  # 각 문서의 앞부분 500자 출력  

#2. 벡터 인덱스 만들기 
index = VectorStoreIndex.from_documents(documents)

#3. 쿼리 엔진 만들기
query_engine = index.as_query_engine()

#4. 질문하기
response = query_engine.query("마울 무덤에 있던 남자를 죽인 사람은 누구니? 한글로 번역해서 답해줘")
print(response)

 

PENGUIN   READERS  2000  
 
 
  
 
  
 
www.penguinreaders.com
 
 
The Adventures of                 
Tom Sawyer 
 
MARK TWAIN 
Level 1 
 
Retold by Jacqueline Kehl                                                    
Series Editors: Andy Hopkins and Jocelyn Potter 
Pearson Education Limited                                                                            
Edinburgh Gate, Harlow,                                                                               
Essex CM20 2JE, England                                                                              
and Associated Companies throughout the world. 
ISBN 0 582 41923 9 
 
First published 1876                                                                                  
Published by Puffin 
Introduction 
 
 
One Saturday afternoon Tom wanted to have an adventure                    
because he didn’t want to think about Injun Joe. He went 
to Huck and said, “I’m going to  look for treasure. Do you 
want to come with m

2025-09-29 17:36:32,747 - INFO - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2025-09-29 17:36:33,203 - INFO - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2025-09-29 17:36:33,976 - INFO - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


인쥰 조가 닥터를 칼로 죽인 사람입니다.
